# Python 爬蟲範例：以 Ptt Web 為例

- 目標網站：https://www.ptt.cc/bbs/index.html

In [15]:
!pip install pyvirtualdisplay selenium webdriver_manager fake_useragent

In [16]:
import urllib.request
from pyvirtualdisplay import Display
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.support.ui import Select
from bs4 import BeautifulSoup
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.chrome.service import Service
from fake_useragent import UserAgent

import re
import os
import time
import random
import warnings
import json

warnings.filterwarnings("ignore")

ua = UserAgent()

service = Service()
options = webdriver.ChromeOptions()
options.add_argument('--headless')
options.add_argument('--no-sandbox')
options.add_argument('--disable-dev-shm-usage')
driver = webdriver.Chrome(service = service, options = options)

In [17]:
board_name = "Movie"
url = "https://www.ptt.cc/bbs/{0}/index.html".format(board_name)
print(url)
driver.get(url)

# driver.find_element("xpath", "/html/body/div[2]/form/div[1]/button").click() # 同意已經滿 18 歲
prev_page = driver.find_element("xpath", '//*[@id="action-bar-container"]/div/div[2]/a[2]').get_attribute("href")
tokens = prev_page.split("index")
last_page_no = int(tokens[1].split(".")[0]) + 1
curr_page_no = last_page_no

https://www.ptt.cc/bbs/Movie/index.html


In [18]:
last_page_no

9699

In [19]:
curr_page_no

9699

In [20]:
%%time

lookback = 1
page_cnt = 0
keys = ["網址", "發文者", "標題", "時間戳記", "推文"]

output = []
print("Start from the first page: {0}".format(curr_page_no))
while page_cnt < lookback:
    page_cnt += 1
    url = tokens[0] + "index" + str(curr_page_no) + ".html"
    driver.get(url)
    for idx in range(2, 23):
        driver.get(url)
        try:
            content_url = driver.find_element("xpath", '//*[@id="main-container"]/div[2]/div[{0}]/div[2]/a'.format(idx)).get_attribute("href")
            driver.get(content_url)
            author = driver.find_element("xpath", '//*[@id="main-content"]/div[1]/span[2]').text
            title = driver.find_element("xpath", '//*[@id="main-content"]/div[3]/span[2]').text
            timestamp = driver.find_element("xpath", '//*[@id="main-content"]/div[4]/span[2]').text
            pushes = []
            for idxx in range(5, 100000):
                try:
                    push_author = driver.find_element("xpath", '//*[@id="main-content"]/div[{0}]/span[2]'.format(idxx)).text
                    push_up = driver.find_element("xpath", '//*[@id="main-content"]/div[{0}]/span[1]'.format(idxx)).text
                    push_context = driver.find_element("xpath", '//*[@id="main-content"]/div[{0}]/span[3]'.format(idxx)).text
                    pushes.append({push_author : (push_up, push_context)})
                except:
                    break
            values = [content_url, author, title, timestamp, pushes]
            output.append({item[0] : item[1] for item in zip(keys, values)})
        except:
            break
    curr_page_no -= 1
    print("Jump to the previos page: {0}".format(curr_page_no))

# print(output)
json_object = json.dumps(output, indent = 4)
with open("./Stock.json", "w", encoding = "utf8") as outfile:
    outfile.write(json_object)

Start from the first page: 9699
Jump to the previos page: 9698
CPU times: user 3.52 s, sys: 128 ms, total: 3.65 s
Wall time: 49.4 s


In [23]:
json_object = json.dumps(output, indent = 4, ensure_ascii = False)
with open("./{0}.json".format(board_name), "w", encoding = "utf8") as outfile:
    outfile.write(json_object)

lookback = 3
page_cnt = 0
keys = ["推文數", "標題", "發文者", "x", "日期"]

output = []
print("Start from the first page: {0}".format(curr_page_no))
while page_cnt < lookback:
    page_cnt += 1
    url = tokens[0] + "index" + str(curr_page_no) + ".html"
    driver.get(url)
    for idx in range(2, 23):
        try:
            page_url = driver.find_element("xpath", '/html/body/div[2]/div[2]/div[{0}]'.format(idx))
            if page_url.text == '':
                continue
            if page_url.text[0] != "[":
                output.append({item[0] : item[1] for item in zip(keys, page_url.text.split("\n"))})
            else:
                output.append({item[0] : item[1] for item in zip(keys[1:], page_url.text.split("\n"))})
        except:
            break
        time.sleep(1)
    curr_page_no -= 1
    print("Jump to the previos page: {0}".format(curr_page_no))
        
output